In [ ]:
%load_ext autoreload
%autoreload 2

In [ ]:
import os
import numpy as np
from tensorflow import keras
from tensorflow.keras import layers

import tensorflow as tf
import tensorflowjs as tfjs

import wandb
from wandb.keras import WandbCallback

import dataset
import schedulers

assert tf.config.list_physical_devices('GPU')

In [ ]:

# masked version of accuracy and sce
def accuracy(real, pred):
    acc = tf.keras.metrics.sparse_categorical_accuracy(real, pred)

    mask = tf.cast(tf.math.logical_not(tf.math.equal(real, 0)), dtype=acc.dtype)
    acc *= mask

    return tf.reduce_sum(acc) / tf.reduce_sum(mask)

def sparse_categorical_crossentropy(y_true, y_pred, sample_weight=None):
    loss = tf.keras.losses.sparse_categorical_crossentropy(y_true, y_pred)

    mask = tf.cast(tf.math.logical_not(tf.math.equal(y_true, 0)), dtype=loss.dtype)
    loss *= mask

    return tf.reduce_sum(loss) / tf.reduce_sum(mask) 

def get_xy(d):
    if d is None:
        return None
    x = d.normalized
    y = {'N': d.niqqud, 'D': d.dagesh, 'S': d.sin }
    return (x, y)


In [ ]:
corpus = {}
corpus['mix'] = dataset.read_corpora([
    'hebrew_diacritized_private/poetry',
    'hebrew_diacritized_private/rabanit',
    'hebrew_diacritized_private/pre_modern'])

corpus['modern'] = dataset.read_corpora([
    'hebrew_diacritized/modern'])


In [13]:
LETTERS_SIZE = len(dataset.letters_table)
NIQQUD_SIZE = len(dataset.niqqud_table)
DAGESH_SIZE = len(dataset.dagesh_table)
SIN_SIZE = len(dataset.sin_table)

def build_model(units, dropout):
    inp = keras.Input(shape=(None,), batch_size=None)
    embed = layers.Embedding(LETTERS_SIZE, units, mask_zero=True)(inp)
    
    layer = layers.Bidirectional(layers.LSTM(units, return_sequences=True, dropout=dropout), merge_mode='concat')(embed)
    layer = layers.add([layer, layers.Bidirectional(layers.LSTM(units, return_sequences=True, dropout=dropout), merge_mode='concat')(layer)])
    layer = layers.Dense(units)(layer)

    outputs = [
        layers.Softmax(name='N')(layers.Dense(NIQQUD_SIZE)(layer)),
        layers.Softmax(name='D')(layers.Dense(DAGESH_SIZE)(layer)),
        layers.Softmax(name='S')(layers.Dense(SIN_SIZE)(layer)),
    ]
    return keras.Model(inputs=inp, outputs=outputs)


In [14]:
MAXLEN = 90
np.random.seed(2)

data = {}
data['mix'] = dataset.load_data(corpus['mix'], validation_rate=0.1, maxlen=MAXLEN)
data['modern'] = dataset.load_data(corpus['modern'], validation_rate=0.2, maxlen=MAXLEN)


In [15]:
%env WANDB_MODE dryrun

def experiment():
    BATCH_SIZE = 64
    UNITS = 500
    np.random.seed(2)
    model = build_model(units=UNITS, dropout=0.1)
    model.compile(loss=sparse_categorical_crossentropy, optimizer=tf.keras.optimizers.Adam(learning_rate=1e-4),
                  metrics={'N': accuracy, 'D': accuracy, 'S': accuracy})

    model.save_weights('./checkpoints/uninit')
    
    config = {
        'batch_size': BATCH_SIZE,
        'maxlen': MAXLEN,
        'units': UNITS,
        'model': model,
        'order': [
            ('mix',    [(30e-4, 80e-4, 1e-4)], 'mix'),
            ('modern', [(40e-4, 40e-4, 1e-5)], 'modern'),
            ('modern', [(40e-4, 40e-4, 1e-5),
                        (40e-4, 40e-4, 1e-5),
                       ], 'modern_over'),
        ],
    }

    run = wandb.init(project="dotter",
                     group="dropout",
                     name=f'dropout_{dropout}',
                     tags=['CLR', 'ordered'],
                     config=config)

    with run:
        for kind, clrs, save in config['order']:
            train, validation = data[kind]

            training_data = (x, y) = get_xy(train)
            validation_data = get_xy(validation)

            wandb_callback = WandbCallback(log_batch_frequency=10,  # int(len(train.normalized) / BATCH_SIZE / 100),
                                           training_data=training_data,
                                           validation_data=validation_data,
                                           log_weights=True)
            for clr in clrs:
                scheduler = schedulers.CircularLearningRate(*clr)
                scheduler.set_dataset(train, BATCH_SIZE)
                callbacks = [wandb_callback, scheduler]
                history = model.fit(x, y, validation_data=validation_data,
                                    batch_size=BATCH_SIZE, verbose=1, callbacks=callbacks)
            model.save(os.path.join(wandb.run.dir, save + ".h5"))
            model.save_weights('./checkpoints/' + save)
    return model

model = experiment()

env: WANDB_MODE=dryrun


204/204 [==============================] - 35s 170ms/step - loss: 0.1031 - N_loss: 0.0602 - D_loss: 0.0326 - S_loss: 0.0103 - N_accuracy: 0.9800 - D_accuracy: 0.9881 - S_accuracy: 0.9971


In [ ]:
model.load_weights('./checkpoints/modern_over')

model.compile()
model.save('modern.h5')
tfjs.converters.save_keras_model(model, '.')

In [ ]:
import matplotlib.pyplot as plt

fig, ax = plt.subplots(nrows=2, ncols=3)

for n, v in enumerate(['accuracy', 'loss'], 0):
    for n1, t in enumerate(['N', 'D', 'S'], 0):
        p = ax[n][n1]
        p.plot(history.history[t + '_' + v][0:])
        p.plot(history.history['val_' + t + '_' +  v][0:])
        p.legend([t + '_Train', t + '_Test'], loc='center right')

plt.tight_layout()

In [16]:
np.random.seed(3)
test, _ = dataset.load_data(dataset.read_corpora(['test/modernTestCorpus/']), 0, MAXLEN)

In [18]:
model = build_model(units=500, dropout=0.1)
model.load_weights('./checkpoints/modern')
x = test.normalized
y = {'N': test.niqqud, 'D': test.dagesh, 'S': test.sin }

model.compile(loss=sparse_categorical_crossentropy,
              metrics={'N': accuracy, 'D': accuracy, 'S': accuracy})

_ = model.evaluate(x=x, y=y, batch_size=64)

7/7 [==============================] - 0s 59ms/step - loss: 0.3670 - N_loss: 0.2075 - D_loss: 0.0925 - S_loss: 0.0670 - N_accuracy: 0.9309 - D_accuracy: 0.9660 - S_accuracy: 0.9828


In [20]:
model.load_weights('./checkpoints/modern_over')

def real_evaluation(data, s=slice(0, None), print_comparison=True):
    batch = data.normalized[s]
    prediction = model.predict(batch)
    [actual_niqqud, actual_dagesh, actual_sin] = [dataset.from_categorical(prediction[0]), dataset.from_categorical(prediction[1]), dataset.from_categorical(prediction[2])]
    [expected_niqqud, expected_dagesh, expected_sin] = [data.niqqud[s], data.dagesh[s], data.sin[s]]
    actual = dataset.merge(data.text[s], batch, actual_niqqud, actual_dagesh, actual_sin)
    expected = dataset.merge(data.text[s], batch, expected_niqqud, expected_dagesh, expected_sin)
    total_letters = []
    total_words = []
    for i, (b, a, e) in enumerate(zip(batch, actual, expected)):
        letters = []
        letters.extend(expected_niqqud[i][expected_niqqud[i]>0] == actual_niqqud[i][expected_niqqud[i]>0])
        letters.extend(expected_dagesh[i][expected_dagesh[i]>0] == actual_dagesh[i][expected_dagesh[i]>0])
        letters.extend(expected_sin[i][expected_sin[i]>0] == actual_sin[i][expected_sin[i]>0])
        total_letters.extend(letters)
        words = []
        for aw, ew in zip(a.split(), e.split()):
            if len([x for x in 'אבגדהוזחטיכלמנסעפצקרשתךםןףץ' if x in aw]) > 1:
                words.append(aw == ew)
                if print_comparison and aw != ew:
                    print(aw, ew)
        total_words.extend(words)
        if print_comparison:
            print('מצוי: ', a)
            print('רצוי: ', e)
            print(f'{np.mean(letters):.2%} ({len(letters)-np.sum(letters)} out of {len(letters)})')
            print(f'{np.mean(words):.2%} ({len(words)-np.sum(words)} out of {len(words)})')
            print()
    print(f'letters: {np.mean(total_letters):.2%}, words: {np.mean(total_words):.2%}')

real_evaluation(test, s=slice(0, None), print_comparison=True)  # 75 - 95.11%, words: 77.78%

פְּרֶס. פֶּרֶס.
מצוי:  שִׁמְעוֹן פְּרֶס.
רצוי:  שִׁמְעוֹן פֶּרֶס.
92.86% (1 out of 14)
50.00% (1 out of 2)

סְנוֹקֶר סְנוּקֶר
מצוי:  מִשְׂחֲקוֹ הַמָּהִיר. קַרְיֵירָה הִיגִינְס הֵחֵל לְשַׂחֵק סְנוֹקֶר מִקְצוֹעָנִי בְּעוֹנַת 1971/1972, בְּגִיל 22. הוּא זָכָה 
רצוי:  מִשְׂחֲקוֹ הַמָּהִיר. קַרְיֵירָה הִיגִינְס הֵחֵל לְשַׂחֵק סְנוּקֶר מִקְצוֹעָנִי בְּעוֹנַת 1971/1972, בְּגִיל 22. הוּא זָכָה 
98.08% (2 out of 104)
91.67% (1 out of 12)

א-פּוֹלִיטִיִּים, אַ-פּוֹלִיטִיִּים,
מצוי:  מִמְּנִיעִים א-פּוֹלִיטִיִּים, סוֹצְיוֹלוֹגִיִּים אוֹ מִגְדָּרִיִּים, לָרוֹב מִתּוֹךְ אִידֵאוֹלוֹגְיָה שֶׁל צְדָקָה וּגְמִילוּת חֲסָדִים. 
רצוי:  מִמְּנִיעִים אַ-פּוֹלִיטִיִּים, סוֹצְיוֹלוֹגִיִּים אוֹ מִגְדָּרִיִּים, לָרוֹב מִתּוֹךְ אִידֵאוֹלוֹגְיָה שֶׁל צְדָקָה וּגְמִילוּת חֲסָדִים. 
99.21% (1 out of 127)
91.67% (1 out of 12)

בָּאִיאן בָּאיָאן
מְבָארִין[1] מִבָּאָרִין[1]
וְאג'וּ. וְאָג'וּ.
קוֹבְּלָאֵי קוּבְּלַאי
כְּ"מִשְׁמָר כְּ"מִשְׁמַר
("מִשַׁמָר ("מִשְׁמָר
מצוי:  שֶׁל בָּאִיאן מְבָארִין[1] וְאג'וּ. בִּסְבִיבוֹת 

C:\Users\elaza\AppData\Local\Programs\Python\Python38\lib\site-packages\numpy\core\fromnumeric.py:3334: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
C:\Users\elaza\AppData\Local\Programs\Python\Python38\lib\site-packages\numpy\core\_methods.py:161: RuntimeWarning: invalid value encountered in double_scalars
  ret = ret.dtype.type(ret / rcount)



90.00% (1 out of 10)

לְמִשְׁמֵר לְמִשְׁמַר
הַדִּילְמָה הַדִּילֵמָה
מצוי:  הַקִּיבּוּצִים סָמוּךְ לְמִשְׁמֵר הָעֵמֶק. הֲקָמָה הָרַעְיוֹן לַהֲקָמַת הָאַנְדַּרְטָה נִתְקַל בְּהִתְנַגְּדוּיוֹת רַבּוֹת. הַדִּילְמָה הָעִיקָּרִית 
רצוי:  הַקִּיבּוּצִים סָמוּךְ לְמִשְׁמַר הָעֵמֶק. הֲקָמָה הָרַעְיוֹן לַהֲקָמַת הָאַנְדַּרְטָה נִתְקַל בְּהִתְנַגְּדוּיוֹת רַבּוֹת. הַדִּילֵמָה הָעִיקָּרִית 
98.54% (2 out of 137)
84.62% (2 out of 13)

יִזְרָעָאל, יִזְרְעֶאל,
לַג'וֹעָרָה לְג'וֹעָרָה
וּלְמְעָרַת וְלִמְעָרַת
בַּקִּיבּוּץ בְּקִיבּוּץ
מִשְׁמָר מִשְׁמַר
מצוי:  הֱיוֹתוֹ צוֹפֶה עַל עֵמֶק יִזְרָעָאל, עֶרֶשׂ הַהִתְיַישְּׁבוּת, וְקִרְבָתוֹ לַג'וֹעָרָה וּלְמְעָרַת הַפַּלְמָ"ח בַּקִּיבּוּץ מִשְׁמָר הָעֵמֶק, 
רצוי:  הֱיוֹתוֹ צוֹפֶה עַל עֵמֶק יִזְרְעֶאל, עֶרֶשׂ הַהִתְיַישְּׁבוּת, וְקִרְבָתוֹ לְג'וֹעָרָה וְלִמְעָרַת הַפַּלְמָ"ח בְּקִיבּוּץ מִשְׁמַר הָעֵמֶק, 
92.74% (9 out of 124)
64.29% (5 out of 14)

הַקְּרָאִים[3]. הַקָּרָאִים[3].
הָרא"ם הָרְאֵ"ם
מַקֵל מֵקֵל
לְהֲתָּרַת לְהַתָּרַת
הָרא"ם הָרְאֵ"ם
מצוי:  הַקְּרָא

requests_with_retry encountered retryable exception: 500 Server Error: Internal Server Error for url: https://api.wandb.ai/files/elazarg/dotter/3g8awyjv/file_stream. args: ('https://api.wandb.ai/files/elazarg/dotter/3g8awyjv/file_stream',), kwargs: {'json': {'files': {'output.log': {'offset': 30, 'content': ['2020-07-19T23:49:16.681179 סְנוֹקֶר סְנוּקֶר\n', '2020-07-19T23:49:16.684178 מצוי:  מִשְׂחֲקוֹ הַמָּהִיר. קַרְיֵירָה הִיגִינְס הֵחֵל לְשַׂחֵק סְנוֹקֶר מִקְצוֹעָנִי בְּעוֹנַת 1971/1972, בְּגִיל 22. הוּא זָכָה \n', '2020-07-19T23:49:16.687178 רצוי:  מִשְׂחֲקוֹ הַמָּהִיר. קַרְיֵירָה הִיגִינְס הֵחֵל לְשַׂחֵק סְנוּקֶר מִקְצוֹעָנִי בְּעוֹנַת 1971/1972, בְּגִיל 22. הוּא זָכָה \n', '2020-07-19T23:49:16.687178 98.08% (2 out of 104)\n', '2020-07-19T23:49:16.688180 91.67% (1 out of 12)\n', '2020-07-19T23:49:16.688180 \n', '2020-07-19T23:49:16.688180 א-פּוֹלִיטִיִּים, אַ-פּוֹלִיטִיִּים,\n', '2020-07-19T23:49:16.688180 מצוי:  מִמְּנִיעִים א-פּוֹלִיטִיִּים, סוֹצְיוֹלוֹגִיִּים אוֹ מִגְדָּרִיִּים

In [ ]:
import hebrew
import dataset

In [ ]:
%env WANDB_MODE run
config = {
        'batch_size': 64,
        'units': 500,
        'order': [
            ('mix',    [(30e-4, 80e-4, 1e-4)], 'mix'),
            ('modern', [(50e-4, 50e-4, 1e-5)], 'modern'),
            ('modern', [(50e-4, 50e-4, 1e-5),
                        # (50e-4, 50e-4, 1e-5),
                       ], 'modern_over'),
        ],
    }
run = wandb.init(project="dotter",
                 # group="maxlen",
                 name=f'maxlen_test',
                 tags=['CLR', 'ordered'],
                 config=config)

with run:
    for maxlen, letters, words in [
            (75, 0.9511, 0.7778),
            (80, 0.9531, 0.7819),
            (85, 0.9535, 0.7819),
            (90, 0.9526, 0.7841),
            (95, 0.9514, 0.7795),
    ]:
        run.log({'maxlen': maxlen,
                 'letters': letters,
                 'words': words})
